In [ ]:
!git clone https://github.com/nateraw/huggingface-vit-finetune.git
!pip install adversarial-robustness-toolbox
!pip install timm
%cd huggingface-vit-finetune/
!pip install -r requirements.txt
!pip install git+https://github.com/huggingface/transformers.git@master --upgrade

Cloning into 'huggingface-vit-finetune'...
remote: Enumerating objects: 24, done.
remote: Counting objects: 100% (24/24), done.
remote: Compressing objects: 100% (17/17), done.
remote: Total 24 (delta 10), reused 19 (delta 6), pack-reused 0
Unpacking objects: 100% (24/24), done.
     |████████████████████████████████| 962kB 16.6MB/s 
     |████████████████████████████████| 3.2MB 48.5MB/s 
     |████████████████████████████████| 6.8MB 52.5MB/s 
     |████████████████████████████████| 21.6MB 1.5MB/s 
     |████████████████████████████████| 235kB 56.6MB/s 
     |████████████████████████████████| 25.3MB 136kB/s 
     |████████████████████████████████| 747kB 54.2MB/s 
  Found existing installation: llvmlite 0.34.0
    Uninstalling llvmlite-0.34.0:
      Successfully uninstalled llvmlite-0.34.0
  Found existing installation: numba 0.51.2
    Uninstalling numba-0.51.2:
      Successfully uninstalled numba-0.51.2
  Found existing installation: scikit-learn 0.22.2.post1
    Uninstalling scikit-

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader

import torchvision
import torchvision.transforms as transforms
import torchvision.datasets as datasets

import matplotlib
import matplotlib.pyplot as plt
import numpy as np

import art
from art.attacks.evasion import FastGradientMethod, ProjectedGradientDescentPyTorch
from art.estimators.classification import PyTorchClassifier

from transformers import ViTFeatureExtractor, ViTForImageClassification
import requests

import timm
from timm.data import resolve_data_config
from timm.data.transforms_factory import create_transform

In [ ]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda')

# 1. Loading CIFER-10 Test DataSet

In [ ]:
cifar_classes = [
    'airplane', 'automobile', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck'
]

In [ ]:
transform = transforms.Compose(
    [transforms.Resize((224, 224)),
     transforms.ToTensor(),
    transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))
     ])
#cifar_trainset = datasets.CIFAR10(root='./data', train=True, download=True, transform=transform)
cifar_testset_224 = datasets.CIFAR10(root='./data', train=False, download=True, transform=transform)
#cifar_trainloader = torch.utils.data.DataLoader(cifar_trainset, batch_size=64, shuffle=True, num_workers=2)
cifar_testloader_224 = torch.utils.data.DataLoader(cifar_testset_224, batch_size=64, shuffle=False, num_workers=2)


Extracting ./data/cifar-10-python.tar.gz to ./data


In [ ]:
transforms = transforms.Compose([transforms.ToTensor(), transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))])
#cifar_trainset = datasets.CIFAR10(root='./data', train=True, download=True, transform=transform)
cifar_testset_32 = datasets.CIFAR10(root='./data', train=False, download=True, transform=transforms)
#cifar_trainloader = torch.utils.data.DataLoader(cifar_trainset, batch_size=64, shuffle=True, num_workers=2)
cifar_testloader_32 = torch.utils.data.DataLoader(cifar_testset_32, batch_size=64, shuffle=False, num_workers=2)

Files already downloaded and verified


In [ ]:
result_dict = {}

# 2. Loading Transformer Model

In [ ]:
model = ViTForImageClassification.from_pretrained('nateraw/vit-base-patch16-224-cifar10', return_dict=False)
model = model.to(device)

In [ ]:
class Transformer(nn.Module):
  def __init__(self, model):
    super(Transformer, self).__init__()
    self.model = model
  def forward(self, x):
    return model(x)[0]

Transformer_Model = Transformer(model).to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.01)
transformer_classifier = PyTorchClassifier(
    model=Transformer_Model.cpu(),
    loss=criterion,
    optimizer=optimizer,
    input_shape=(3, 224, 224),
    nb_classes=10,
)

In [ ]:
# cifar-10 DATASET consists of 60000 images
correct = 0
total = 0
with torch.no_grad():
  for i, (inputs, labels) in enumerate(cifar_testloader_224):
    inputs, labels = inputs.to(device), labels.to(device)
    outputs = Transformer_Model(inputs)
    _, predicted = torch.max(outputs, 1)
    total += labels.size(0)
    correct += (predicted == labels).sum().item()
    if(i % 10 == 0):
      print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))

print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer"] = 100 * correct / total

Accuracy of the network on 64 cifar-10 test images: 98.437500 %
Accuracy of the network on 704 cifar-10 test images: 99.147727 %
Accuracy of the network on 1344 cifar-10 test images: 98.809524 %
Accuracy of the network on 1984 cifar-10 test images: 98.739919 %
Accuracy of the network on 2624 cifar-10 test images: 98.780488 %
Accuracy of the network on 3264 cifar-10 test images: 98.743873 %
Accuracy of the network on 3904 cifar-10 test images: 98.796107 %
Accuracy of the network on 4544 cifar-10 test images: 98.811620 %
Accuracy of the network on 5184 cifar-10 test images: 98.688272 %
Accuracy of the network on 5824 cifar-10 test images: 98.677885 %
Accuracy of the network on 6464 cifar-10 test images: 98.623144 %
Accuracy of the network on 7104 cifar-10 test images: 98.606419 %
Accuracy of the network on 7744 cifar-10 test images: 98.592459 %
Accuracy of the network on 8384 cifar-10 test images: 98.520992 %
Accuracy of the network on 9024 cifar-10 test images: 98.548316 %
Accuracy of t

# 3. Loading CNN_MODEL

In [ ]:
CNN_Model = torch.hub.load("chenyaofo/pytorch-cifar-models", "cifar10_vgg16_bn", pretrained=True)
CNN_Model = CNN_Model.to(device)
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.01)
cnn_classifier = PyTorchClassifier(
    model=CNN_Model,
    loss=criterion,
    optimizer=optimizer,
    input_shape=(3, 32, 32),
    nb_classes=10,
)

Downloading: "https://github.com/chenyaofo/pytorch-cifar-models/archive/master.zip" to /root/.cache/torch/hub/master.zip
Downloading: "https://github.com/chenyaofo/pytorch-cifar-models/releases/download/vgg/cifar10_vgg16_bn-6ee7ea24.pt" to /root/.cache/torch/hub/checkpoints/cifar10_vgg16_bn-6ee7ea24.pt


In [ ]:
correct = 0
total = 0
with torch.no_grad():
  for i, (inputs, labels) in enumerate(cifar_testloader_32):
    inputs, labels = inputs.to(device), labels.to(device)
    outputs = CNN_Model(inputs)
    _, predicted = torch.max(outputs, 1)
    total += labels.size(0)
    correct += (predicted == labels).sum().item()
    if(i % 10 == 0):
      print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN"] = 100 * correct / total

Accuracy of the network on 64 cifar-10 test images: 90.625000 %
Accuracy of the network on 704 cifar-10 test images: 93.750000 %
Accuracy of the network on 1344 cifar-10 test images: 92.782738 %
Accuracy of the network on 1984 cifar-10 test images: 92.187500 %
Accuracy of the network on 2624 cifar-10 test images: 91.920732 %
Accuracy of the network on 3264 cifar-10 test images: 92.248775 %
Accuracy of the network on 3904 cifar-10 test images: 92.136270 %
Accuracy of the network on 4544 cifar-10 test images: 92.407570 %
Accuracy of the network on 5184 cifar-10 test images: 92.341821 %
Accuracy of the network on 5824 cifar-10 test images: 92.427885 %
Accuracy of the network on 6464 cifar-10 test images: 92.465965 %
Accuracy of the network on 7104 cifar-10 test images: 92.412725 %
Accuracy of the network on 7744 cifar-10 test images: 92.445764 %
Accuracy of the network on 8384 cifar-10 test images: 92.485687 %
Accuracy of the network on 9024 cifar-10 test images: 92.398050 %
Accuracy of t

# 4. Parameters

In [ ]:
eps = 0.05

## 5. PGD-Attack on CNN 

In [ ]:
attack_PGD_1 = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=eps,
        max_iter=1
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader_32):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_1.generate(x=inputs,batch_size = 64)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_1"] = 100 * correct / total

Accuracy of the network on 64 cifar-10 test images: 35.937500 %


/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 704 cifar-10 test images: 40.625000 %


Accuracy of the network on 1344 cifar-10 test images: 41.071429 %


Accuracy of the network on 1984 cifar-10 test images: 41.229839 %


...

Accuracy of the network on 7744 cifar-10 test images: 40.379649 %


Accuracy of the network on 8384 cifar-10 test images: 40.195611 %


Accuracy of the network on 9024 cifar-10 test images: 40.203901 %


Accuracy of the network on 9664 cifar-10 test images: 40.200745 %


Accuracy of the network on 10000 cifar-10 test images: 40.190000 %


In [ ]:
attack_PGD_5 = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=5
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader_32):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_5.generate(x=inputs,batch_size = 64)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_5"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 9.375000 %


Accuracy of the network on 704 cifar-10 test images: 5.681818 %


Accuracy of the network on 1344 cifar-10 test images: 6.696429 %


Accuracy of the network on 1984 cifar-10 test images: 6.905242 %


...

Accuracy of the network on 7744 cifar-10 test images: 7.153926 %


Accuracy of the network on 8384 cifar-10 test images: 7.120706 %


Accuracy of the network on 9024 cifar-10 test images: 7.092199 %


Accuracy of the network on 9664 cifar-10 test images: 6.995033 %


Accuracy of the network on 10000 cifar-10 test images: 6.930000 %


In [ ]:
attack_PGD_10 = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=10
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader_32):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_10.generate(x=inputs,batch_size = 64)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_10"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 6.250000 %


Accuracy of the network on 704 cifar-10 test images: 3.835227 %


Accuracy of the network on 1344 cifar-10 test images: 4.538690 %


Accuracy of the network on 1984 cifar-10 test images: 4.838710 %


...

Accuracy of the network on 7744 cifar-10 test images: 4.881198 %


Accuracy of the network on 8384 cifar-10 test images: 4.818702 %


Accuracy of the network on 9024 cifar-10 test images: 4.809397 %


Accuracy of the network on 9664 cifar-10 test images: 4.749586 %


Accuracy of the network on 10000 cifar-10 test images: 4.700000 %


In [ ]:
attack_PGD_20 = ProjectedGradientDescentPyTorch(
        estimator=cnn_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.01,
        max_iter=20
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader_32):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_20.generate(x=inputs)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["CNN_PGD_20"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 6.250000 %


Accuracy of the network on 704 cifar-10 test images: 3.693182 %


Accuracy of the network on 1344 cifar-10 test images: 4.315476 %


Accuracy of the network on 1984 cifar-10 test images: 4.586694 %


...

Accuracy of the network on 7744 cifar-10 test images: 4.622934 %


Accuracy of the network on 8384 cifar-10 test images: 4.568225 %


Accuracy of the network on 9024 cifar-10 test images: 4.587766 %


Accuracy of the network on 9664 cifar-10 test images: 4.490894 %


Accuracy of the network on 10000 cifar-10 test images: 4.460000 %


# 6. PGD-Attack on Transformer

In [ ]:
attack_PGD_1 = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=eps,
        max_iter=1
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader_224):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_1.generate(x=inputs,batch_size = 64)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_1"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 48.437500 %


Accuracy of the network on 704 cifar-10 test images: 42.329545 %


Accuracy of the network on 1344 cifar-10 test images: 43.526786 %


Accuracy of the network on 1984 cifar-10 test images: 44.254032 %


...

Accuracy of the network on 7744 cifar-10 test images: 44.679752 %


Accuracy of the network on 8384 cifar-10 test images: 45.014313 %


Accuracy of the network on 9024 cifar-10 test images: 44.869238 %


Accuracy of the network on 9664 cifar-10 test images: 44.857202 %


Accuracy of the network on 10000 cifar-10 test images: 44.840000 %


In [ ]:
attack_PGD_5 = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=5
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader_224):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_5.generate(x=inputs,batch_size = 64)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_5"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 1.562500 %


Accuracy of the network on 704 cifar-10 test images: 0.994318 %


Accuracy of the network on 1344 cifar-10 test images: 1.041667 %


Accuracy of the network on 1984 cifar-10 test images: 1.310484 %


...

Accuracy of the network on 7744 cifar-10 test images: 1.601240 %


Accuracy of the network on 8384 cifar-10 test images: 1.681775 %


Accuracy of the network on 9024 cifar-10 test images: 1.651152 %


Accuracy of the network on 9664 cifar-10 test images: 1.779801 %


Accuracy of the network on 10000 cifar-10 test images: 1.780000 %


In [ ]:
attack_PGD_10 = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.02,
        max_iter=10
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader_224):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_10.generate(x=inputs,batch_size = 64)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_10"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 1.562500 %


Accuracy of the network on 704 cifar-10 test images: 0.852273 %


Accuracy of the network on 1344 cifar-10 test images: 0.967262 %


Accuracy of the network on 1984 cifar-10 test images: 1.008065 %


...

Accuracy of the network on 7744 cifar-10 test images: 0.891012 %


Accuracy of the network on 8384 cifar-10 test images: 0.954198 %


Accuracy of the network on 9024 cifar-10 test images: 0.941933 %


Accuracy of the network on 9664 cifar-10 test images: 0.983030 %


Accuracy of the network on 10000 cifar-10 test images: 0.980000 %


In [ ]:
attack_PGD_20 = ProjectedGradientDescentPyTorch(
        estimator=transformer_classifier,
        norm="inf",
        eps=eps,
        targeted=False,
        eps_step=0.01,
        max_iter=20
)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader_224):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_PGD_20.generate(x=inputs)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))
result_dict["Transformer_PGD_20"] = 100 * correct / total

/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:670: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  x_grad = torch.tensor(x).to(self._device)
/usr/local/lib/python3.7/dist-packages/art/estimators/classification/pytorch.py:671: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  y_grad = torch.tensor(y).to(self._device)


Accuracy of the network on 64 cifar-10 test images: 1.562500 %


Accuracy of the network on 704 cifar-10 test images: 0.852273 %


Accuracy of the network on 1344 cifar-10 test images: 0.892857 %


Accuracy of the network on 1984 cifar-10 test images: 1.008065 %


...

Accuracy of the network on 7744 cifar-10 test images: 0.929752 %


Accuracy of the network on 8384 cifar-10 test images: 0.978053 %


Accuracy of the network on 9024 cifar-10 test images: 0.941933 %


Accuracy of the network on 9664 cifar-10 test images: 0.962334 %


Accuracy of the network on 10000 cifar-10 test images: 0.960000 %


# 7. Result

## I have recorded the result at the end of our experiment tracker doc
https://docs.google.com/document/d/1PjEIoUyZk_LQAZjJ4JzRZR45T6lKYRuhROd3u3X72ao/edit

In [ ]:
result_dict

In [ ]:
print(result_dict)

# 8. FGM Attack

In [ ]:
attack_FGM = FastGradientMethod(estimator=transformer_classifier, eps=eps)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_FGM.generate(x=inputs)
  outputs = transformer_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))

In [ ]:
attack_FGM = FastGradientMethod(estimator=cnn_classifier, eps=eps)
correct = 0
total = 0
for i, (inputs, labels) in enumerate(cifar_testloader):
  inputs, labels = inputs.cpu(), labels.numpy()
  x_test_adv = attack_FGM.generate(x=inputs)
  outputs = cnn_classifier.predict(x_test_adv)
  predicted = np.argmax(outputs, 1)
  total += labels.size
  correct += (predicted == labels).sum().item()
  if(i % 10 == 0):
    print('Accuracy of the network on %d cifar-10 test images: %f %%' % (total, 100 * correct / total))


print('Accuracy of the network on %d cifar-10 test images: %f %%' % (
    total,
    100 * correct / total))